In [9]:
from IPython import get_ipython
get_ipython().magic('reset -sf')


In [10]:
import numpy as np
import pandas as pd
from sklearn.model_selection import GridSearchCV, train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.base import BaseEstimator, ClassifierMixin
from scipy.optimize import minimize, LinearConstraint, NonlinearConstraint
import pickle

In [11]:
## 定义超圆盘分类器类
class NHCmodel(BaseEstimator, ClassifierMixin):
    def __init__(self, sigma=0) -> None:
        super().__init__()
        self.sigma = sigma
        self.classes = 0
        self.s_r = {}
        self.classifiers = {}
        self.predictData = None
        self.accuracy = 0

    def gaussian_kernel(self, x, y):
        return np.exp(-np.linalg.norm(x-y, ord=2, axis=1)**2 / (2 * (self.sigma ** 2)))
    
    def Objective_Function1(self, beta, X):
        """返回超圆盘的对偶问题的目标函数，在某一拉格朗日系数下的值
        Args:
            beta (ndarray): 为该输入样本集合下的拉格朗日系数
            X (ndarray): X为输入样本矩阵, 行为样本个数, 列为样本特征
        """
        beta = beta.reshape(-1, 1)
        print(X)
        return np.sum(beta*np.sum(X*X, 1).reshape(-1, 1))-np.sum((beta*X)@((beta*X).T))
    
    def Objective_Function2(self, alpha, X_plus, X_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        result = 0
        for i in range(M_plus):
            result = result + np.sum(alpha_plus[i]*alpha_plus*self.gaussian_kernel(X_plus[i, :], X_plus))
            - 2*np.sum(alpha_plus[i]*alpha_minus*self.gaussian_kernel(X_plus[i, :], X_minus))
        for i in range(M_minus):
            result = result + np.sum(alpha_minus[i]*alpha_minus*self.gaussian_kernel(X_minus[i, :], X_minus))
        return result
    
    def nonlcon(self, alpha, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        
        c = np.zeros((2, 1))
        for i in range(M_plus):
            c[0] = c[0] + np.sum(alpha_plus[i]*alpha_plus*self.gaussian_kernel(X_plus[i, :],X_plus))
            - np.sum(alpha_plus[i]*beta_plus*self.gaussian_kernel(X_plus[i, :], X_plus))
            + np.sum(beta_plus[i]*beta_plus*self.gaussian_kernel(X_plus[i, :], X_plus))
        c[0] -= r_plus**2
        for i in range(M_minus):
            c[0] = c[0] + np.sum(alpha_minus[i]*alpha_minus*self.gaussian_kernel(X_minus[i, :],X_minus))
            - np.sum(alpha_minus[i]*beta_minus*self.gaussian_kernel(X_minus[i, :], X_minus))
            + np.sum(beta_minus[i]*beta_minus*self.gaussian_kernel(X_minus[i, :], X_minus))
        c[1] -= r_minus**2
        return c.flatten()

    def fit(self, X, y):
        # 拟合函数
        classes = np.unique(y)
        Num = np.size(classes)
        beta = np.zeros((Num, np.size(y)))
        s_and_r = np.ones((Num, np.shape(X)[1]+1))
        # 分类求解超圆盘对偶问题拉格朗日系数，以求解s和r
        for i in classes:
            Xx = X[y==i, :]
            M = np.shape(Xx)[0]
            # 设定拉格朗日系数beta初值,一个样本一个beta
            beta_init = np.ones((M, 1)) / M # 一维数组，但是在优化函数里面需要reshape乘二维数组才能运算
            # 设线性等式约束
            Aeq1 = np.ones((1, M))
            beq1 = np.array([1])
            linearConstraint1 = LinearConstraint(Aeq1, beq1, beq1)
            # 设定beta下界
            bounds = [(1e-6, None) for _ in range(M)] 
            # 求解beta
            result1 = minimize(self.Objective_Function1, beta_init, 
                            args=(Xx,), method='SLSQP', bounds=bounds, constraints=linearConstraint1,
                            )
            beta[i-1, :M] = result1.x
            
            s = np.sum(result1.x.reshape(-1, 1)*Xx, 0)
            r = np.max(np.linalg.norm(Xx-s, ord=2,axis=1))
            s_and_r[i-1, :] = np.concatenate([s, [r]])
            
            self.s_r = {'s': s,
                        'r': r}
        # 求解多个分类器的参数，即分类超平面参数，OVO策略
        Num_classifier = int(Num*(Num-1)/2)
        b_classifier = np.zeros((Num_classifier, 1))
        iter = 0
        for i in range(Num-1):
            for j in range(i+1, Num):
                iter += 1
                # 获取基本信息
                X_plus = X[y==i+1, :]
                X_minus = X[y==j+1, :]
                M_plus = np.shape(X_plus)[0]
                M_minus = np.shape(X_minus)[0]
                # 设定超平面参数初值，都为列
                alpha_plus = np.ones((M_plus, 1)) / M_plus
                alpha_minus = np.ones((M_minus, 1)) / M_minus
                alpha_init = np.concatenate((alpha_plus, alpha_minus), axis=0)
                # 设定线性等式约束
                Aeq2 = np.zeros((2, M_plus+M_minus))
                Aeq2[0,:M_plus] = 1;
                Aeq2[1, M_plus:] = 1
                beq2 = np.array([1, 1])
                linearConstraint2 = LinearConstraint(Aeq2, beq2, beq2)
                # 设定不等式约束
                r_plus = s_and_r[i, -1]
                r_minus = s_and_r[j, -1]
                beta_plus = beta[i, :M_plus]
                beta_minus = beta[j, :M_minus]
                lb = -np.inf
                ub = np.array([0, 0])
                # NonlinearConstraint(lambda x: NHCmodel.nonlcon(x, beta_plus, beta_minus, X_plus, X_minus, r_plus_minus), lb, ub)
                # 这个和@(beta)Objective_Function1(beta, X),@(beta) 表示输入要优化的值为beta，X不动，异曲同工
                nonlinearConstraint =  NonlinearConstraint(lambda x: NHCmodel.nonlcon(self, x, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus), lb, ub)
                constraints = [linearConstraint2, nonlinearConstraint]
                # 求解alpha
                result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
                                   method='SLSQP', constraints=constraints)
                alpha = result2.x
                alpha_plus = alpha[:M_plus]
                alpha_minus = alpha[M_plus:]
                # 求解b
                for k in range(M_plus):
                    b_classifier[iter-1] += np.sum(alpha_plus[k]*alpha_plus*self.gaussian_kernel(X_plus[k, :], X_plus))
                for k in range(M_minus):
                    b_classifier[iter-1] -= np.sum(alpha_minus[k]*alpha_minus*self.gaussian_kernel(X_minus[k, :], X_minus))
                b_classifier[iter-1] = -1/2*b_classifier[iter-1]
                b = b_classifier[iter-1]
                self.classes = Num
                self.classifiers[(i+1, j+1)] = {'X+': X_plus,
                                                'X-': X_minus,
                                                'alpha+': alpha_plus,
                                                'alpha-': alpha_minus,
                                                'b': b}    
        # 保存分类器参数字典
        with open('classifiers.pkl', 'wb') as f:
            pickle.dump(self.classifiers, f)                                  
        return 0  
                

    def predict(self,X):
        fx = np.zeros((np.shape(X)[0], self.classes))
        indexclasses = 0
        fxij = np.zeros((np.shape(X)[0], self.classes))
        for (i, j), classifier in self.classifiers.items():
            indexclasses += 1
            X_pl = classifier['X+']
            X_mi = classifier['X-']
            alpha_pl = classifier['alpha+']
            alpha_mi = classifier['alpha-']
            bb = classifier['b']
            
            M_plus = np.shape(X_pl)[0]
            M_minus = np.shape(X_mi)[0]
            
            for g in range(M_plus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] + alpha_pl[g]*self.gaussian_kernel(X_pl[g, :], X).reshape(-1)
            for g in range(M_minus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] - alpha_mi[g]*self.gaussian_kernel(X_mi[g, :], X).reshape(-1)
            
            fx[:, indexclasses-1] = np.sign(fx[:, indexclasses-1] + bb)
            fxij[:, indexclasses-1] = fx[:, indexclasses-1] 
            fx[:, indexclasses-1][fx[:, indexclasses-1]==1] = i
            fx[:, indexclasses-1][fx[:, indexclasses-1]==-1] = j
            fx[:, indexclasses-1][fx[:, indexclasses-1]==0] = 0


        y_pred = np.apply_along_axis(lambda x: np.argmax(np.bincount(x.astype(int))), axis=1, arr=fx) # axis表示假如你是n×m维度，axis=0，表示在n方向上，axis=1，表示在m方向上
        y_pred = y_pred.reshape(-1, 1)
        self.predictData = np.concatenate((X, y_pred, fxij, fx), axis=1)
        return y_pred
    
    def score(self, X, y):
        y_pred = self.predict(X)
        y = y.reshape(-1, 1)
        accuray = np.sum(y_pred==y) / np.size(y)
        self.accuracy = accuray
        return accuray
              

In [12]:
## 划分测试集和训练集
train_ratio = 0.8 # 训练集比例

data = pd.read_csv('seeds_dataset.txt', header=None, delim_whitespace=True) # delim_whitespace=True表示分割符为空白字符
data.info
Data = data.iloc[:, :-1].values
labels = data.iloc[:, -1].values

# 划分
X_train, X_test, Y_train, Y_test = train_test_split(Data, labels, train_size=train_ratio, stratify=labels)

# 使用StandardScaler类归一化
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)



手搓数据集划分

classes = labels.unique()
trainData = pd.DataFrame(data=None, index=None)
testData = pd.DataFrame(data=None, index=None)

for i in classes:
    classData = data.loc[labels==i, :]
    numTrain = round(train_ratio*classData.shape[0]) # 训练集样本数
    indices = np.random.permutation(classData.shape[0])
    
    trainData = pd.concat([trainData, classData.iloc[indices[0:numTrain], :]])
    testData = pd.concat([testData, classData.iloc[indices[numTrain:], :]])

trainData.info
testData.info                                            
trainData.to_csv('trainData.csv', header=0, index=0, sep='\t')
testData.to_csv('testData.csv', header=0, index=0, sep='\t')


In [13]:
"""# 网格搜索最佳sigma
param_grid = {'sigma': (2 ** np.arange(-5, 5.5, 0.5)).tolist()}

testmodel = NHCmodel()
grid_search = GridSearchCV(testmodel, param_grid=param_grid, cv=5)

grid_search.fit(Data, labels)
sigma = grid_search.best_params_
score = grid_search.best_score_
print(sigma, score)
"""

sigma = 0.25

In [14]:
## 训练
model = NHCmodel(sigma) # 必须有输入值！！
model.fit(X_train_scaled, Y_train)

C:\Users\lenovo\AppData\Local\Temp\ipykernel_18468\112712606.py:76: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(self.Objective_Function1, beta_init,


[[-2.71086589e-01 -1.23759217e-01 -7.95724892e-01  1.86205916e-01
  -2.01557668e-01  1.59938168e-01 -2.22886387e-01]
 [ 1.30305350e-01  2.12080773e-01 -7.61021099e-02  1.79544849e-01
  -5.25162044e-02  5.78695150e-01 -1.92967158e-01]
 [-2.47071686e-01 -1.31391944e-01 -5.58723377e-01  5.52049196e-02
  -3.53260586e-01 -4.10055283e-01 -4.68224069e-01]
 [ 1.64612353e-01  1.43386229e-01  6.34902436e-01  1.50680222e-01
   3.49363456e-01 -1.55609165e+00 -5.55987142e-01]
 [-4.90651410e-01 -4.21435571e-01 -4.72541008e-01 -2.60085615e-01
  -5.23593687e-01 -1.01532884e-01 -6.25798678e-01]
 [ 4.45378418e-02  1.43386229e-01 -2.44157730e-01  3.46071539e-01
  -4.45318403e-02 -1.27109492e+00 -8.17281747e-01]
 [-2.91670791e-01 -3.14577393e-01  3.54809736e-01 -4.33273373e-01
  -1.61635847e-01 -1.32083491e+00 -8.17281747e-01]
 [-6.18138684e-02 -2.76413758e-01  1.89316503e+00 -9.50616292e-01
   5.43649649e-01 -1.28722681e+00 -1.51938633e+00]
 [-3.70576898e-01 -4.06170117e-01  3.46191499e-01 -5.70935437e-0

d:\software\Anaconda3\lib\site-packages\scipy\optimize\_optimize.py:284: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  warnings.warn("Values in x were outside bounds during a "


[[-2.71086589e-01 -1.23759217e-01 -7.95724892e-01  1.86205916e-01
  -2.01557668e-01  1.59938168e-01 -2.22886387e-01]
 [ 1.30305350e-01  2.12080773e-01 -7.61021099e-02  1.79544849e-01
  -5.25162044e-02  5.78695150e-01 -1.92967158e-01]
 [-2.47071686e-01 -1.31391944e-01 -5.58723377e-01  5.52049196e-02
  -3.53260586e-01 -4.10055283e-01 -4.68224069e-01]
 [ 1.64612353e-01  1.43386229e-01  6.34902436e-01  1.50680222e-01
   3.49363456e-01 -1.55609165e+00 -5.55987142e-01]
 [-4.90651410e-01 -4.21435571e-01 -4.72541008e-01 -2.60085615e-01
  -5.23593687e-01 -1.01532884e-01 -6.25798678e-01]
 [ 4.45378418e-02  1.43386229e-01 -2.44157730e-01  3.46071539e-01
  -4.45318403e-02 -1.27109492e+00 -8.17281747e-01]
 [-2.91670791e-01 -3.14577393e-01  3.54809736e-01 -4.33273373e-01
  -1.61635847e-01 -1.32083491e+00 -8.17281747e-01]
 [-6.18138684e-02 -2.76413758e-01  1.89316503e+00 -9.50616292e-01
   5.43649649e-01 -1.28722681e+00 -1.51938633e+00]
 [-3.70576898e-01 -4.06170117e-01  3.46191499e-01 -5.70935437e-0

C:\Users\lenovo\AppData\Local\Temp\ipykernel_18468\112712606.py:76: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(self.Objective_Function1, beta_init,


...

[[ 1.45112498  1.28829528  1.5829085   1.15650143  1.77856463 -0.50146933
   1.33291355]
 [ 1.46484778  1.4333171   0.75986687  1.35855382  1.47249734 -0.40198934
   1.54434277]
 [ 0.85075242  0.90665893  0.30740943  1.13651823  0.83108676 -0.10489369
   1.1174951 ]
 [ 1.33105047  1.24249892  1.16492401  1.19646784  1.4219297  -0.3777915
   1.28105355]
 [ 0.24694916  0.41053168 -0.57595985  0.44154684  0.0645878  -0.64329553
   0.68067434]
 [ 1.40652587  1.52490982 -0.11488418  1.81150642  0.77253475 -1.0338217
   2.07889967]
 [ 1.46141708  1.55544073  0.03593497  1.3896388   1.26490387  2.01644986
   1.28105355]
 [ 0.56600429  0.5860844   0.47115593  0.53702214  0.5463111   1.24346346
   0.9359851 ]
 [ 0.91593573  0.83033166  1.19508784  0.35051225  1.1398155   1.13188455
   0.49916435]
 [ 2.16127995  2.01340435  1.1864696   2.08683055  2.05269447  1.41015965
   1.63609507]
 [ 1.81134851  1.87601527  0.09195351  1.95360919  1.36071624 -1.19110763
   1.54434277]
 [ 1.82507131  1.769157

C:\Users\lenovo\AppData\Local\Temp\ipykernel_18468\112712606.py:76: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(self.Objective_Function1, beta_init,


[[-1.26942038 -1.16944282 -1.92902305 -0.91731095 -1.51365484 -0.23529314
  -0.81728175]
 [-0.92291965 -0.92519556 -0.58026897 -0.87290384 -0.93878062  0.78975405
  -0.50412714]
 [-1.13905377 -0.96335919 -2.2220431  -0.59980006 -1.54026938  0.25538519
  -0.45625638]
 [-0.88518195 -0.94046101 -0.12781153 -0.86624277 -0.76578606  1.31404048
  -0.6936156 ]
 [-0.83029074 -0.88703192 -0.03301093 -0.88178526 -0.65134351  0.87713512
  -0.52606791]
 [-0.94350385 -0.64278466 -2.72620996 -0.53096903 -1.37525919  0.76824486
  -0.380461  ]
 [-1.26598968 -1.16181009 -1.98504159 -0.85070028 -1.56156102  1.432341
  -0.38245561]
 [-0.71364693 -0.84123556  0.63059332 -1.05053231 -0.36124495  0.80050864
  -0.99081328]
 [-0.57641892 -0.69621374  0.72970304 -0.88178526 -0.07913075  3.11409055
  -0.70757791]
 [-1.18365288 -1.10074828 -1.63169387 -1.01500661 -1.44445701 -0.98206522
  -0.55598714]
 [-1.36204929 -1.35262827 -1.47225649 -1.21039793 -1.56156102  0.33402815
  -0.90703944]
 [-1.07387047 -0.803071

C:\Users\lenovo\AppData\Local\Temp\ipykernel_18468\112712606.py:121: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
C:\Users\lenovo\AppData\Local\Temp\ipykernel_18468\112712606.py:121: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
C:\Users\lenovo\AppData\Local\Temp\ipykernel_18468\112712606.py:121: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(self.Objective_Function2, alpha_init, args=(X_plus, X_minus,),


0

In [15]:
# 测试
model.predict(X_test_scaled)

array([[2],
       [2],
       [1],
       [2],
       [1],
       [1],
       [3],
       [3],
       [2],
       [1],
       [1],
       [3],
       [3],
       [3],
       [1],
       [2],
       [2],
       [2],
       [3],
       [1],
       [3],
       [2],
       [2],
       [1],
       [3],
       [3],
       [3],
       [2],
       [1],
       [2],
       [2],
       [1],
       [1],
       [1],
       [1],
       [2],
       [3],
       [1],
       [1],
       [2],
       [3],
       [1]], dtype=int64)

In [16]:
accuracy = model.score(X_test_scaled, Y_test)
print(accuracy)

0.9047619047619048
